# HW3 Q4 [10 pts]



## Important Notices

<div class="alert alert-block alert-danger">
    WARNING: Do <strong>NOT</strong> add any cells to this Jupyter Notebook, because that will crash the autograder.
</div>


All instructions, code comments, etc. in this notebook **are part of the assignment instructions**. That is, if there is instructions about completing a task in this notebook, that task is not optional.  



<div class="alert alert-block alert-info">
    You <strong>must</strong> implement the following functions in this notebook to receive credit.
</div>

`user()`

`load_data()`

`exclude_no_pickuplocations()`

`exclude_no_tripdistance()`

`include_fare_range()`

`get_highest_tip()`

`get_total_toll()`

Each method will be auto-graded using different sets of parameters or data, to ensure that values are not hard-coded.  You may assume we will only use your code to work with data from NYC Taxi Trips during auto-grading. You do not need to write code for unreasonable scenarios.  

Since the overall correctness of your code will require multiple function to work together correctly (i.e., all methods are interdepedent), implementing only a subset of the functions likely will lead to a low score.

### Helper functions

You are permitted to write additional helper functions, or use additional instance variables so long as the previously described functions work as required.  

#### Pyspark Imports
<span style="color:red">*Please don't modify the below cell*</span>

In [ ]:
import pyspark
from pyspark.sql import SQLContext

#### Define Spark Context
<span style="color:red">*Please don't modify the below cell*</span>

In [ ]:
sc
sqlContext = SQLContext(sc)

### Student Section - Please compete all the functions below

#### Function to return GT Username

In [85]:
def user():
        """
        :return: string
        your GTUsername, NOT your 9-Digit GTId  
        """         
        return 'helfayoumy3'

#### Function to load data

In [86]:
def load_data(gcp_storage_path):
    """
        :param gcp_storage_path: string (full gs path including file name e.g gs://bucket_name/data.csv) 
        :return: spark dataframe  
    """
    df = sqlContext.read.option("header",True).csv("gs://helfayoumy3/yellow_tripdata_2019-01.csv")
    
    ################################################################
    # code to load yellow_tripdata_2019-01.csv data from your GCP storage bucket#
    #                                                              #        
    ################################################################
        
    return df

#### Function to exclude trips that don't have a pickup location

In [89]:
def exclude_no_pickuplocations(df):
    """
        :param nyc tax trips dataframe: spark dataframe 
        :return: spark dataframe  
    """
    from pyspark.sql.functions import col

    df = df.withColumn("PULocationID", col("PULocationID").cast('string'))
    df = df.where(df.PULocationID.isNotNull())
    
    ################################################################
    # code to exclude trips with no pickup locations               #
    #                                                              #        
    ################################################################
    
    return df

#### Function to exclude trips with no distance

In [93]:
def exclude_no_tripdistance(df):
    """
        :param nyc tax trips dataframe: spark dataframe 
        :return: spark dataframe  
    """
    from pyspark.sql.functions import col

    df = df.withColumn("trip_distance", col("trip_distance").cast('float'))
    df = df.where(df.trip_distance.isNotNull())
    df = df.where(df.trip_distance != '0.0')
    
    ################################################################
    # code to exclude trips with no trip distances                 #
    #                                                              #        
    ################################################################
    
    return df

#### Function to include fare amount between the range of 20 to 60 Dollars

In [99]:
def include_fare_range(df):
    """
        :param nyc tax trips dataframe: spark dataframe 
        :return: spark dataframe  
    """
    from pyspark.sql.functions import col
    #df = df.withColumn("fare_amount", col("fare_amount").cast('float'))
    df = df.filter(col("fare_amount").between(20,60))

    
    ################################################################
    # code to include trips with only within the fare range of     #
    # 20 to 60 dollars                                             #        
    ################################################################
    
    return df

#### Function to get the highest tip amount

In [122]:
def get_highest_tip(df):
    """
        :param nyc tax trips dataframe: spark dataframe 
        :return: float (rounded to 2 digits)  
    """
    import pyspark.sql.functions as F
    from pyspark.sql.functions import col

    df = df.withColumn("tip_amount", col("tip_amount").cast('float'))
    max_tip = round(df.agg(F.max(F.abs(df.tip_amount))).first()[0],2)
    
    #max_tip = df.orderBy("tip_amount", ascending=False).collect()[0][13]

    ################################################################
    # code to get the highest tip                                  #
    #                                                              #        
    ################################################################
    
    return max_tip

#### Function to get total toll amount

In [135]:
def get_total_toll(df):
    """
        :param nyc tax trips dataframe: spark dataframe 
        :return: float (rounded to 2 digits)  
    """
    from pyspark.sql import functions as F
    from pyspark.sql.functions import col

    df = df.withColumn("tolls_amount", col("tolls_amount").cast('float'))
    total_toll = round(df.groupBy().agg(F.sum("tolls_amount")).collect()[0][0],2)
    
    ################################################################
    # code to get total toll amount                                #
    #                                                              #        
    ################################################################
    
    return total_toll

### Run above functions and print

#### Uncomment the cells below and test your implemented functions

#### Load data from yellow_tripdata_2019-01.csv 

In [44]:
gcp_storage_path = "gs://helfayoumy3/yellow_tripdata_2019-01.csv"
df = load_data(gcp_storage_path)
df.printSchema()

root
 |-- VendorID: string (nullable = true)
 |-- tpep_pickup_datetime: string (nullable = true)
 |-- tpep_dropoff_datetime: string (nullable = true)
 |-- passenger_count: string (nullable = true)
 |-- trip_distance: string (nullable = true)
 |-- RatecodeID: string (nullable = true)
 |-- store_and_fwd_flag: string (nullable = true)
 |-- PULocationID: string (nullable = true)
 |-- DOLocationID: string (nullable = true)
 |-- payment_type: string (nullable = true)
 |-- fare_amount: string (nullable = true)
 |-- extra: string (nullable = true)
 |-- mta_tax: string (nullable = true)
 |-- tip_amount: string (nullable = true)
 |-- tolls_amount: string (nullable = true)
 |-- improvement_surcharge: string (nullable = true)
 |-- total_amount: string (nullable = true)
 |-- congestion_surcharge: string (nullable = true)



#### Print total numbers of rows in the dataframe

In [45]:
df.count()

7667792

#### Print total number of rows in the dataframe after excluding trips with no pickup location

In [91]:
df_no_pickup_locations = exclude_no_pickuplocations(df)
df_no_pickup_locations.count()

7667792

#### Print total number of rows in the dataframe after exclude trips with no distance

In [94]:
df_no_trip_distance = exclude_no_tripdistance(df_no_pickup_locations)
df_no_trip_distance.count()

7613022

#### Print total number of rows in the dataframe after including trips with fair amount between the range of 20 to 60 Dollars

In [100]:
df_include_fare_range = include_fare_range(df_no_trip_distance)
df_include_fare_range.count()

957922

#### Print the highest tip amount

In [123]:
max_tip = get_highest_tip(df_include_fare_range)
print(max_tip)

444.8


#### Print the total toll amount

In [136]:
total_toll = get_total_toll(df_include_fare_range)
print(total_toll)

2096233.31
